In [30]:
#!/usr/bin/python3.6

## import packages
import os
import sys
import cv2
import pandas as pd
import glob
import matplotlib.pyplot as plt
import matplotlib
matplotlib.use("Agg")
from tqdm import tqdm
import numpy as np
import json

In [32]:
with open(r'./data/iwildcam2020_megadetector_results.json') as f:
    detections = json.loads(f.read())

In [33]:
detector_results_images = pd.DataFrame.from_records(detections['images'])

In [34]:
with open(r'./data/iwildcam2020_train_annotations.json') as json_file:
    train_data = json.load(json_file)

trainAnno_annotations = pd.DataFrame.from_records(train_data['annotations'])
trainAnno_annotations.head()

trainAnno_categories = pd.DataFrame.from_records(train_data['categories'])

trainAnno_images = pd.DataFrame.from_records(train_data['images'])

In [35]:
with open(r'./data/iwildcam2020_test_information.json') as json_file:
    test_data = json.load(json_file)

trainAnno_annotations = pd.DataFrame.from_records(train_data['annotations'])
trainAnno_annotations.head()

trainAnno_categories = pd.DataFrame.from_records(train_data['categories'])

testAnno_images = pd.DataFrame.from_records(test_data['images'])

In [36]:
## output folder
OUTPUT = "./data/animal_crops_test"
DATASET = "./data/test"
assert DATASET and OUTPUT

"""
extract objects from images
"""
def extract_objects(img_path, show=False):
    objects = []
    confidences = []
    categories = []
    
    # split out image_id
    img_id = img_path.split('/')[-1].split('.')[0] 
    img = cv2.imread(img_path)

    if not (detector_results_images[detector_results_images.id == img_id].detections.values):
        return None

    # convert from str dict
    detections = detector_results_images[detector_results_images.id == img_id].detections.values[0]


    annotation = trainAnno_annotations[trainAnno_annotations.image_id == img_id]

    cat_id = annotation.category_id
    cat_name = trainAnno_categories[trainAnno_categories.id == int(cat_id)].name.values[0]
    
    # loop over bboxes dict
    for idx, detection in enumerate(detections):
        # save confidence
        confidences.append(detection["conf"])

        # distinguish human or animal
        if detection['category'] == "1":
            categories.append(cat_name)
        else:
            categories.append('human')

        x_rel, y_rel, w_rel, h_rel = detection['bbox']    
        img_height, img_width, _ = img.shape
        x = float(x_rel * img_width)
        y = float(y_rel * img_height)
        w = float(w_rel * img_width)
        h = float(h_rel * img_height)

        img_obj = img[int(y):int(y+h), int(x):int(x+w), :]
        objects.append(img_obj)
        
        # display or not
        if show:
            cv2.imshow("crop", obj)
            cv2.waitKey(0)
    
    return (objects, categories, confidences)

In [37]:
## list all raw images to be croped
imagePaths = list(glob.glob(os.path.sep.join([DATASET, "*.jpg"])))
print("[INFO] crop animals from %d images.." % len(imagePaths))

[INFO] crop animals from 62894 images..


In [38]:
for path in tqdm(imagePaths):
    image_id = path.split("/")[-1].split(".")[0]
    print(path)

    try:
        items = extract_objects(path, show=False)
        if items is None: 
            continue

        # store images to different folder
        animals, categories, confidences = np.array(items[0]), np.array(items[1]), np.array(items[2]) 
        
        # only save confidence score > threshold value=0.3
        idxs = confidences > 0.3
        animals = animals[idxs]
        categories = categories[idxs]
        confidences = confidences[idxs]

        # double check if there are 2 types of animals in ONE image
        if len(set(categories)) > 1:
            print("got %d types of objects in image!" % len(set(categories)))

        cat_counts = {}
        # loop over animals & save
        for i in range(len(animals)):
            class_folder = OUTPUT
            image_name = image_id + ".jpg"
            img = animals[i]
            image = cv2.resize(img, (224, 224))
            cv2.imwrite(os.path.sep.join([class_folder, image_name]), image)
            pass
    except:
        continue

print("[INFO] Done!")


  0%|          | 0/62894 [00:00<?, ?it/s]<ipython-input-38-c4798a35644b>:14: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  animals, categories, confidences = np.array(items[0]), np.array(items[1]), np.array(items[2])
  0%|          | 1/62894 [00:00<2:02:49,  8.53it/s]

./data/test/8f88ed26-21bc-11ea-a13a-137349068a90.jpg
./data/test/8ff9fdf4-21bc-11ea-a13a-137349068a90.jpg
./data/test/97ae6fbc-21bc-11ea-a13a-137349068a90.jpg


  0%|          | 4/62894 [00:00<1:51:39,  9.39it/s]

./data/test/8c2a0c0a-21bc-11ea-a13a-137349068a90.jpg
./data/test/8f7bf2ba-21bc-11ea-a13a-137349068a90.jpg
./data/test/92118e36-21bc-11ea-a13a-137349068a90.jpg


  0%|          | 7/62894 [00:00<1:41:52, 10.29it/s]

...

./data/test/94cf75e8-21bc-11ea-a13a-137349068a90.jpg
./data/test/90058ef8-21bc-11ea-a13a-137349068a90.jpg
./data/test/9090ede0-21bc-11ea-a13a-137349068a90.jpg
./data/test/989549a0-21bc-11ea-a13a-137349068a90.jpg


100%|█████████▉| 62892/62894 [1:26:51<00:00, 15.85it/s]

./data/test/88799efe-21bc-11ea-a13a-137349068a90.jpg
./data/test/8838b812-21bc-11ea-a13a-137349068a90.jpg
./data/test/9501962c-21bc-11ea-a13a-137349068a90.jpg
./data/test/8808a3d4-21bc-11ea-a13a-137349068a90.jpg


100%|██████████| 62894/62894 [1:26:52<00:00, 12.07it/s]

./data/test/945646d2-21bc-11ea-a13a-137349068a90.jpg
[INFO] Done!
